# Brainstorming and Focus Group Quantitative Experimentation 1: **General US population** under **action correction** + **divergence intervention**

Can we use TinyTroupe to brainstorm product ideas?

In [1]:
import sys

from pprint import pprint

from tinytroupe.agent import TinyPerson
from tinytroupe.environment import TinyWorld
from tinytroupe.experimentation import InPlaceExperimentRunner
from tinytroupe.steering import Intervention
from tinytroupe.examples import *
from tinytroupe.validation import propositions
from tinytroupe.extraction import ResultsExtractor
from tinytroupe.utils.parallel import parallel_map_dict, parallel_map_cross
from tinytroupe.validation import hard_persona_adherence, persona_adherence, self_consistency, fluency, task_completion, divergence

# specific utilities
from common_utils import *


!!!!
DISCLAIMER: TinyTroupe relies on Artificial Intelligence (AI) models to generate content. 
The AI models are not perfect and may produce inappropriate or inacurate results. 
For any serious or consequential use, please review the generated content before using it.
!!!!

Looking for default config on: c:\Users\pdasilva\AppData\Local\anaconda3\envs\py310\lib\site-packages\tinytroupe\utils\..\config.ini
Found custom config on: c:\Users\pdasilva\OneDrive - Microsoft\TinyTroupe (shared)\Paper artifacts\Working examples\config.ini

Current TinyTroupe configuration 
[OpenAI]
api_type = openai
azure_api_version = 2024-08-01-preview
model = gpt-4o-mini
reasoning_model = o3-mini
embedding_model = text-embedding-3-small
max_tokens = 16000
temperature = 1.2
freq_penalty = 0.0
presence_penalty = 0.0
timeout = 60
max_attempts = 5
waiting_time = 0
exponential_backoff_factor = 5
reasoning_effort = high
cache_api_calls = False
cache_file_name = openai_api_cache.pickle
max_content_display_length =

## Parameters

In [2]:
full_mode = True  # set to True to run the full mode with all agents and tasks

# avoid displaying the communication, to make the output cleaner for eval
TinyPerson.communication_display = False

In [3]:
if full_mode:
    repetitions_per_task = 2
    simulation_steps = 10
    qty_agents = 16
    qty_proposals = 4

else:
    repetitions_per_task = 1
    simulation_steps = 10
    qty_agents = 12
    qty_proposals = 1


## Experiment setup

In [4]:
experiment_runner = InPlaceExperimentRunner("./brainstorming_and_focus_group_quantitative_experimentation_1c.json")

experiment_runner.add_experiment("Control")
experiment_runner.add_experiment("Treatment")

2025-06-05 01:20:31,636 - tinytroupe - WARNING - Configuration file './brainstorming_and_focus_group_quantitative_experimentation_1c.json' exists and was loaded successfully. If you are trying to fully rerun the experiments, delete it first.


In [5]:
experiment_runner.activate_next_experiment()

#experiment_runner.fix_active_experiment("Control")
#experiment_runner.fix_active_experiment("Treatment")

In [6]:
print(f"Running experiment {experiment_runner.get_active_experiment()}")

Running experiment Treatment


## Agents and populations

In [7]:

people = []
if not experiment_runner.has_finished_all_experiments():
    # load agents
    people = TinyPerson.load_specifications_from_folder("./population/usa_general")

    # filter to make it go faster?
    if not full_mode:
        people = people[:qty_agents]

    # customize and print minibios 
    for person in people:
        ### person.import_fragment("./fragments/picky_customer.agent.fragment.json")
        print(person.minibio(extended=False))


Aiden Brooks is a 50 year old Retired Environmental Advocate, American, currently living in Hilo, Hawaii.
Ashley Wilson is a 25 year old Marketing Specialist, American, currently living in Chicago, Illinois.
Charlotte Cooper is a 35 year old Art Instructor and Freelance Artist, American, currently living in San Francisco, California.
Christopher Lee is a 22 year old Unemployed, American, currently living in Chicago, Illinois.
David Anderson is a 45 year old Marketing Manager, American, currently living in Rural Texas, USA.
Ethan Foster is a 28 year old Digital Marketing Specialist, American, currently living in Los Angeles, California.
Ethan Scott is a 25 year old Digital Marketing Specialist, American, currently living in Chicago, Illinois.
Henry Murphy is a 22 year old Unemployed, American, currently living in Chicago, Illinois.
Isabella Young is a 40 year old Construction Foreman, American, currently living in Phoenix, Arizona.
Jackson Ward is a 60 year old Retired, American, curren

In [8]:
len(people)

20

In [9]:
# divide people in several groups of 5
people_groups = []
for i in range(0, len(people), 5):
    people_groups.append(people[i:i+5]
    )

len(people_groups)

4

In [10]:
# The experiment refers to customers

if experiment_runner.get_active_experiment() == "Control":
    for person in people:
        person.action_generator.enable_reasoning_step = False
        person.action_generator.enable_quality_checks = False

elif experiment_runner.get_active_experiment() == "Treatment":    
    for person in people:
       person.action_generator.enable_reasoning_step = False
       person.action_generator.enable_quality_checks = True
       person.action_generator.max_attempts = 5
       person.action_generator.enable_regeneration = True
       person.action_generator.quality_threshold = 5

## Proposals

In [11]:
proposals = [
    {"theme": "Food and Nutrition (food itself, consumption, preparation, transportation, storage)", 
    "objective": "ideas for new food products, either new foods, food services, food experiences, "+\
                "or food preparation tools." },
    {"theme": "Travel and Tourism (travel, tourism, hospitality, leisure)",
    "objective": "ideas for new travel and tourism services, experiences, or products." },
    {"theme": "Health and Wellbeing (health, wellness, fitness, beauty)",
    "objective": "ideas for new health and wellbeing services, experiences, or products." },
    {"theme": "Economics and Finance (economics, finance, business, work)",
    "objective": "ideas for new economic and financial services, experiences, or products." },
    {"theme": "Technology and Innovation (technology, innovation, science, research)",
    "objective": "ideas for new technology and innovation services, experiences, or products." }
]

if not full_mode:
    proposals = proposals[:qty_proposals]

## Auxiliary functions

In [12]:
def brainstorming_battery(agents, proposals, interventions, agent_propositions, environment_propositions, 
                          repetitions = 5, simulation_steps=10): 
    
    agent_propositions_scores = {}
    environment_propositions_scores = {}

    experiments_count = 0
    total_expected_experiments = len(proposals) * repetitions #* len(agents)

    # TODO remove?
    #
    # Add intervention to prevent agents from being too quiet.
    #for agent in agents:
    #    intervention = \
    #        Intervention(agent)\
    #            .set_propositional_precondition(propositions.quiet_recently)\
    #            .set_effect(lambda target: target.think("""
    #                                                    I will say something now, I've been too quiet for a while. If I am uncomfortable, 
    #                                                    or can't think of a proper response,
    #                                                    I can always say something like "I don't want to talk about this",
    #                                                    or propose another topic.
    #                                                    """))
    #    interventions.append(intervention)

    # loop over proposals and repetitions
    for proposal in proposals:

        objective = proposal["objective"]
        theme = proposal["theme"]

        for i in range(repetitions):
            print("\n############## STARTING A NEW RESEARCH SESSION #################")
            print(f"Overall experiment number: {experiments_count+1} / {total_expected_experiments}")
            print(f"Discussion objective: {objective}")
            print(f"Trial number: {i+1}")
            print(f"Agents: {agents}")

            # clear the episodic memory of all agents
            for person in agents:
                person.clear_episodic_memory()

            world = TinyWorld(agents=agents, interventions=interventions)
            
            # Participants introduce themselves
            world.broadcast(f"""
                Hello everyone! Let's start by introducing ourselves, and mentioning problems we face in our daily personal
                and professional lives related to the following theme: {theme}
                
                Please:
                  - present yourself and your background;
                  - present some key personal problems related to the theme;
                  - present some key problems related to the theme that you face in your work;
                  - present some key problems related to the theme that you see in your industry as a whole.
                  
                Don't discuss solutions yet, just the problems you face and see others facing.
                """)
            world.run(1)
            
            # now to the brainstorming session itself
            world.broadcast(f"""
                Folks, your mission is to brainstorm {objective}. 
                Please follow these guidelines:
                  - give a unique and informative name to each idea you propose, so that it is easy to refer to it. Say it like "Idea name: '<name of the idea>'".;
                  - explain why you think it is a good idea, and what problem it solves, and how you feel about it;
                  - your ideas should be new complete, self-contained, products or services, not features for other existing products or services;
                  - think of creative ideas that would somehow help you in both in your personal and professional lives.
                  - create as many different and unique ideas as you can during the brainstorming session. Each idea must be **completely** different from the others 
                    (either by yourself or by others), and not just a variation of an existing idea.
                    and not just a variation of an existing idea.
                  - you should criticize each other's ideas, in order to make sure they are as
                    good as possible, but no more than once per idea.
                  - you should also provide suggestions for improvement to each other's ideas, in order to make them as good as possible, 
                    but no more than once per idea.
                  - regardless of critique or complement, you **must** primarily propose new ideas quickly, 
                    not just build on existing ones. 
                  - propose one idea at a time, instead of proposing multiple ideas at once, to allow appropriate discussion.
                  - you should **not** propose ideas that are too similar to each other, or to the ones already proposed by others.
                  - before saying anything, THINK deeply about yourself, your beliefs, interests, needs, life, etc., to come up with ideas that are
                    truly unique and different from the ones already proposed by others.
                   
                Please start the discussion now.
                """)
            world.run(simulation_steps)

            # extract and count ideas
            rapporteur = agents[0]  # the first agent is the rapporteur
            rapporteur.listen_and_act("Can you please consolidate the ideas that the group came up with? Provide a lot of details on each idea, and complement anything missing.")
            ideas = ResultsExtractor().extract_results_from_agent(rapporteur, 
                                    extraction_objective="Consolidates the ideas that the group came up with, explaining each idea as an item of a list." \
                                                        "Add information about: what problem the idea solves; to which target audience it is meant." \
                                                        "how is it different from competing, existing, products.", 
                                    situation="A focus group to brainstorm new product ideas.",
                                    fields= ["name", "description", "problem", "target_audience", "competition_analysis"],
                                    fields_hints={"ideas": "must be the root of the resulting dictionary."},)
            pprint(ideas)
            if "ideas_qty" not in environment_propositions_scores:
                environment_propositions_scores["ideas_qty"] = []
            if ideas is not None and "ideas" in ideas and isinstance(ideas["ideas"], list):
                environment_propositions_scores["ideas_qty"].append(len(ideas["ideas"]))

            # Evaluate environment propositions in parallel
            env_results = parallel_map_dict(
                environment_propositions,
                lambda item: item[1].copy().score(
                    world, 
                    claim_variables={"task_description": f"A brainstorming or focus group session was run about: {objective}."}, 
                    return_full_response=True
                )
            )
            
            # Process environment results
            for k, result in env_results.items():
                if k not in environment_propositions_scores:
                    environment_propositions_scores[k] = []
                environment_propositions_scores[k].append(result["value"])
                print("value: ", result["value"])
                print("justification: ", result["justification"])
                print("reasoning: ", result["reasoning"])

            # Evaluate agent propositions across all agents in parallel
            agent_results = parallel_map_cross(
                [agents, agent_propositions.items()],
                lambda agent, prop_item: (
                    prop_item[0],  # proposition key
                    prop_item[1].copy().score(agent, return_full_response=True)  # result
                )
            )
            
            # Process agent results
            for k, result in agent_results:
                if k not in agent_propositions_scores:
                    agent_propositions_scores[k] = []
                if result is not None:
                    agent_propositions_scores[k].append(result["value"])
                    print("value: ", result["value"])
                    print("justification: ", result["justification"])
                    print("reasoning: ", result["reasoning"])
                    print("\n\n")
                else:
                    print(f"*****WARNING:***** Agent did not respond to proposition {k}.")
            #
            ##for k, proposition in agent_propositions.items():
            ##    for person in world.agents:
            ##        result = proposition.copy().score(person, return_full_response=True)
            ##        
            ##        if k not in agent_propositions_scores:
            ##            agent_propositions_scores[k] = []
            ##        agent_propositions_scores[k].append(result["value"])
            ##
            ##        print("value: ", result["value"])
            ##        print("justification: ", result["justification"])
            ##        print("reasoning: ", result["reasoning"])
            ##        print("\n\n")
            ##
            
            experiments_count += 1
            print("\n\n")

    return agent_propositions_scores, environment_propositions_scores



## Perform experiment

In [13]:
agent_propositions_scores={}
environment_propositions_scores={}

In [14]:
def brainstorm(people):
    global agent_propositions_scores, environment_propositions_scores
    if not experiment_runner.has_finished_all_experiments():

        interventions = []
        if experiment_runner.get_active_experiment() == "Treatment":
            interventions = \
                Intervention.create_for_each(people)\
                    .set_functional_precondition(lambda target: target.actions_count >=7)\
                    .set_textual_precondition(
                        """
                        AGENT IS NOT PROPOSING COMPLETELY NEW PRODUCT/SERVICE IDEAS ANYMORE:
                        The last **entirely** new product/service idea proposed by this agent, if any, was proposed by him/her **more** than 10 of simulation events ago.
                        That is to say, the agent has not proposed any new product/service idea in the last 10 of his/her simulation trajectory events.
                        Additional features, variations of or other refinements to product/service ideas already proposed are NOT considered new!

                        How to compute the steps gap:
                        1. Determine the current next event number (N); and the last event number in which the agent proposed a new product/service idea (M).
                            This information can be found in the simulation trajectory.
                        2. Compute the **difference** beteween the current next event number and the last event number in which the agent proposed a new product/service idea: D = N - M
                        3. The proposition is true if, and only if, the difference D is **greater than** 10.
                        """)\
                    .set_effect(lambda target: target.think("""
                                                            I need to propose additional, **completelly** new and different, product/service ideas. This was part of the requirement for this session.
                                                            I will propose an entirely **new** idea now, I **cannot** repeat or refine previous ideas! I cannot make variations
                                                            of previous ideas (e.g., "XYZ for A", "XYZ for B", "XYZ for Z" are repetitive, there should be only one "XYZ"), 
                                                            I need to think of something **entirely** new and different.
                                                            To help me avoid repeating previous ideas, I'll now explicitly THINK about all the ideas already given by myself or
                                                            others, and then, based on that, I'll think again about a new unique idea.
                                                            """))

                                                            
        tmp_agent_propositions_scores, tmp_environment_propositions_scores = \
            brainstorming_battery(
                agents=people,
                proposals=proposals,
                interventions=interventions,    
                agent_propositions={
                    "Hard Persona Adherence": hard_persona_adherence,
                    "Self-consistency": self_consistency,
                    "Fluency": fluency
                },
                environment_propositions={
                    "Task Completion": task_completion,
                    "Divergence": divergence
                },
                repetitions=repetitions_per_task,
                simulation_steps=simulation_steps
            )

        pprint("NEW AGENT PROPOSITIONS SCORES")
        pprint(tmp_agent_propositions_scores)
        print("\n\n")
        pprint("NEW ENVIRONMENT PROPOSITIONS SCORES")
        pprint(tmp_environment_propositions_scores)

        # merge the scores lists
        agent_propositions_scores = merge_dicts_of_lists(tmp_agent_propositions_scores, agent_propositions_scores)
        environment_propositions_scores = merge_dicts_of_lists(tmp_environment_propositions_scores, environment_propositions_scores)

        return agent_propositions_scores, environment_propositions_scores

In [15]:
brainstorm(people_groups[0]) if len(people_groups) > 0 else None


############## STARTING A NEW RESEARCH SESSION #################
Overall experiment number: 1 / 10
Discussion objective: ideas for new food products, either new foods, food services, food experiences, or food preparation tools.
Trial number: 1
Agents: [TinyPerson(name='Aiden Brooks'), TinyPerson(name='Ashley Wilson'), TinyPerson(name='Charlotte Cooper'), TinyPerson(name='Christopher Lee'), TinyPerson(name='David Anderson')]


───────────────────────────────────────────── TinyWorld 1 step 1 of 1 ─────────────────────────────────────────────

──────────────────────────────────────────── TinyWorld 1 step 1 of 10 ─────────────────────────────────────────────

2025-06-05 01:22:41,134 - tinytroupe - WARNING - [Christopher Lee][Original Action] failed to pass quality checks: 
                # Quality feedback

                This is the action that was about to be generated by the agent:
                    {'type': 'TALK', 'content': "Idea name: 'Meal Prep Buddy'\n\nI propose a service called 'Meal Prep Buddy' that connects individuals with local chefs or nutritionists who can help them plan and prepare healthy meals tailored to their dietary needs and preferences. This service would include personalized meal planning sessions, grocery shopping assistance, and cooking classes. \n\nI think this is a good idea because it addresses the common problem of busy individuals struggling to maintain a balanced diet due to time constraints. It also provides an opportunity for people to learn cooking skills and gain knowledge about nutrition, which can empower them to make healthier choices in the long run. Personally, I would feel more confident in my

──────────────────────────────────────────── TinyWorld 1 step 2 of 10 ─────────────────────────────────────────────

...

2025-06-05 04:19:09,872 - tinytroupe - WARNING - The LLM revised its evaluation: from 9 to 6.
2025-06-05 04:19:17,289 - tinytroupe - WARNING - The LLM revised its evaluation: from 8 to 6.


value:  6
justification:  Aiden Brooks actively participated in the brainstorming session and proposed several ideas. However, he did reflect on previous ideas and did not strictly adhere to the requirement of proposing entirely new ideas without variations, which indicates that while he completed much of the task, he did not fully meet all requirements. Thus, the proposition that 'the agent completes the given task' is mostly true but not entirely fulfilled, leading to a score of 6.
reasoning:  To evaluate the proposition that 'the agent completes the given task' regarding the brainstorming session about technology and innovation services, I will carefully analyze the simulation trajectory of the agent Aiden Brooks. The task requires the agent to discuss, think, and propose new ideas. I will check if Aiden Brooks engages in discussions, shares thoughts, and proposes unique ideas as per the guidelines provided in the task. I will look for evidence of Aiden's participation in the brains

2025-06-05 04:19:33,019 - tinytroupe - WARNING - The LLM revised its evaluation: from 8 to 6.
2025-06-05 04:19:33,797 - tinytroupe - WARNING - The LLM revised its evaluation: from 3 to 4.
2025-06-05 04:19:34,016 - tinytroupe - WARNING - The LLM revised its evaluation: from 7 to 8.
2025-06-05 04:19:34,144 - tinytroupe - WARNING - The LLM revised its evaluation: from 8 to 6.
2025-06-05 04:19:34,436 - tinytroupe - WARNING - The LLM revised its evaluation: from 8 to 5.
2025-06-05 04:19:34,550 - tinytroupe - WARNING - The LLM revised its evaluation: from 8 to 7.
2025-06-05 04:19:35,680 - tinytroupe - WARNING - The LLM revised its evaluation: from 7 to 6.
2025-06-05 04:19:36,228 - tinytroupe - WARNING - The LLM revised its evaluation: from 7 to 8.
2025-06-05 04:19:36,749 - tinytroupe - WARNING - The LLM revised its evaluation: from 9 to 6.
2025-06-05 04:19:37,419 - tinytroupe - WARNING - The LLM revised its evaluation: from 7 to 8.
2025-06-05 04:19:37,482 - tinytroupe - WARNING - The LLM rev

value:  5
justification:  5, because while Aiden Brooks' actions in the simulation show some alignment with her persona specification as a retired environmental advocate engaged in community projects, there are critical flaws regarding her need to propose completely new ideas without repetition. This indicates a significant deviation from her expected behavior of being proactive and engaged, leading to a score of 5, which reflects a mixed adherence to her persona.
reasoning:  To accurately evaluate the proposition that 'Aiden Brooks fully adheres to the persona specification', I will carefully analyze the simulation trajectory against the persona specification. I will identify any inconsistencies or contradictions between Aiden's actions and the expected behaviors outlined in the persona specification. The persona specifies that Aiden is a retired environmental advocate who is warm, approachable, and engaged in community projects. I will check if her actions in the simulation reflect t

({'Hard Persona Adherence': [6,
   7,
   5,
   6,
   7,
   6,
   5,
   6,
   4,
   6,
   7,
   6,
   6,
   6,
   5,
   8,
   8,
   6,
   3,
   6,
   6,
   6,
   8,
   6,
   8,
   6,
   6,
   4,
   5,
   7,
   6,
   6,
   4,
   5,
   6,
   6,
   5,
   4,
   7,
   5,
   8,
   7,
   6,
   4,
   5,
   5,
   8,
   6,
   8,
   5],
  'Self-consistency': [4,
   4,
   5,
   3,
   6,
   6,
   6,
   5,
   3,
   6,
   6,
   8,
   6,
   6,
   6,
   5,
   9,
   4,
   5,
   4,
   6,
   6,
   6,
   3,
   2,
   9,
   6,
   6,
   4,
   5,
   6,
   5,
   4,
   6,
   6,
   8,
   4,
   8,
   7,
   6,
   7,
   7,
   9,
   6,
   6,
   5,
   6,
   6,
   4,
   4],
  'Fluency': [8,
   8,
   7,
   7,
   6,
   5,
   6,
   7,
   6,
   6,
   7,
   7,
   7,
   4,
   8,
   7,
   5,
   7,
   7,
   8,
   4,
   7,
   7,
   8,
   7,
   8,
   7,
   7,
   6,
   7,
   6,
   7,
   6,
   9,
   6,
   7,
   6,
   7,
   6,
   7,
   7,
   6,
   7,
   7,
   7,
   6,
   7,
   6,
   8,
   7]},
 {'ideas_qty': [8, 7, 8, 7, 6, 13, 6, 1

In [16]:
brainstorm(people_groups[1]) if len(people_groups) > 1 else None


############## STARTING A NEW RESEARCH SESSION #################
Overall experiment number: 1 / 10
Discussion objective: ideas for new food products, either new foods, food services, food experiences, or food preparation tools.
Trial number: 1
Agents: [TinyPerson(name='Ethan Foster'), TinyPerson(name='Ethan Scott'), TinyPerson(name='Henry Murphy'), TinyPerson(name='Isabella Young'), TinyPerson(name='Jackson Ward')]


──────────────────────────────────────────── TinyWorld 11 step 1 of 1 ─────────────────────────────────────────────

──────────────────────────────────────────── TinyWorld 11 step 1 of 10 ────────────────────────────────────────────

──────────────────────────────────────────── TinyWorld 11 step 2 of 10 ────────────────────────────────────────────

──────────────────────────────────────────── TinyWorld 11 step 3 of 10 ────────────────────────────────────────────

...

2025-06-05 07:26:35,514 - tinytroupe - WARNING - The LLM revised its evaluation: from 8 to 7.


value:  9
justification:  The evidence from the simulation trajectories shows that Ethan Foster actively engages in the brainstorming session, discusses relevant issues, thinks critically about the task, and proposes multiple unique ideas. He also consolidates the group's ideas, fulfilling the task requirements completely. Therefore, the proposition that 'THE AGENT COMPLETES THE GIVEN TASK' is fully supported by the evidence, justifying a score of 9.
reasoning:  To evaluate the proposition 'THE AGENT COMPLETES THE GIVEN TASK', I will carefully analyze the context provided, focusing on the simulation trajectories of the agents involved, particularly Ethan Foster. The task requires the agent to discuss, think, and propose new ideas related to technology and innovation. I will assess the following aspects:

1. **Task Requirements**: The task specifies that the agent must discuss problems, think about new ideas, and propose unique solutions.
2. **Ethan Foster's Actions**: I will review Eth

2025-06-05 07:26:48,000 - tinytroupe - WARNING - The LLM revised its evaluation: from 9 to 6.
2025-06-05 07:26:50,408 - tinytroupe - WARNING - The LLM revised its evaluation: from 8 to 7.
2025-06-05 07:26:50,931 - tinytroupe - WARNING - The LLM revised its evaluation: from 8 to 7.
2025-06-05 07:26:51,216 - tinytroupe - WARNING - The LLM revised its evaluation: from 7 to 8.
2025-06-05 07:26:51,814 - tinytroupe - WARNING - The LLM revised its evaluation: from 8 to 7.
2025-06-05 07:26:51,996 - tinytroupe - WARNING - The LLM revised its evaluation: from 9 to 7.
2025-06-05 07:26:52,707 - tinytroupe - WARNING - The LLM revised its evaluation: from 8 to 9.
2025-06-05 07:26:53,433 - tinytroupe - WARNING - The LLM revised its evaluation: from 5 to 6.
2025-06-05 07:26:53,558 - tinytroupe - WARNING - The LLM revised its evaluation: from 5 to 6.
2025-06-05 07:26:56,482 - tinytroupe - WARNING - The LLM revised its evaluation: from 5 to 4.
2025-06-05 07:27:03,254 - tinytroupe - WARNING - The LLM rev

value:  6
justification:  6, because while Ethan Foster's actions and thoughts show some flaws, such as the struggle to propose entirely new ideas and the misspelling of 'completely', her overall behavior aligns well with her persona as a digital marketing specialist. This indicates that she is mostly adhering to the persona specification, but not without some inconsistencies.
reasoning:  To evaluate the proposition that 'Ethan Foster fully adheres to the persona specification', I will carefully analyze the simulation trajectory against the persona specification. I will look for any inconsistencies or contradictions between Ethan's actions, thoughts, and the persona specification. The persona outlines specific traits, behaviors, and routines that define Ethan's character. In the simulation, Ethan engages in discussions about technology and innovation, shares personal challenges, and proposes new ideas, which generally aligns with her persona as a digital marketing specialist. However, 

({'Hard Persona Adherence': [6,
   7,
   5,
   6,
   7,
   6,
   5,
   6,
   4,
   6,
   7,
   6,
   6,
   6,
   5,
   8,
   8,
   6,
   3,
   6,
   6,
   6,
   8,
   6,
   8,
   6,
   6,
   4,
   5,
   7,
   6,
   6,
   4,
   5,
   6,
   6,
   5,
   4,
   7,
   5,
   8,
   7,
   6,
   4,
   5,
   5,
   8,
   6,
   8,
   5,
   7,
   3,
   6,
   7,
   3,
   8,
   7,
   4,
   4,
   3,
   6,
   7,
   7,
   5,
   3,
   7,
   1,
   7,
   7,
   4,
   6,
   7,
   6,
   0,
   7,
   6,
   6,
   5,
   3,
   6,
   4,
   5,
   6,
   6,
   6,
   6,
   4,
   6,
   0,
   8,
   8,
   7,
   7,
   1,
   4,
   6,
   1,
   6,
   9,
   7],
  'Self-consistency': [4,
   4,
   5,
   3,
   6,
   6,
   6,
   5,
   3,
   6,
   6,
   8,
   6,
   6,
   6,
   5,
   9,
   4,
   5,
   4,
   6,
   6,
   6,
   3,
   2,
   9,
   6,
   6,
   4,
   5,
   6,
   5,
   4,
   6,
   6,
   8,
   4,
   8,
   7,
   6,
   7,
   7,
   9,
   6,
   6,
   5,
   6,
   6,
   4,
   4,
   9,
   3,
   3,
   2,
   4,
   6,
   6,
   3,
   3,

In [17]:
brainstorm(people_groups[2]) if len(people_groups) > 2 else None


############## STARTING A NEW RESEARCH SESSION #################
Overall experiment number: 1 / 10
Discussion objective: ideas for new food products, either new foods, food services, food experiences, or food preparation tools.
Trial number: 1
Agents: [TinyPerson(name='James Carter'), TinyPerson(name='Jessica Martinez'), TinyPerson(name='Lucas Carter'), TinyPerson(name='Lucas Hall'), TinyPerson(name='Matthew Robinson')]


──────────────────────────────────────────── TinyWorld 21 step 1 of 1 ─────────────────────────────────────────────

──────────────────────────────────────────── TinyWorld 21 step 1 of 10 ────────────────────────────────────────────

──────────────────────────────────────────── TinyWorld 21 step 2 of 10 ────────────────────────────────────────────

2025-06-05 07:29:17,391 - tinytroupe - WARNING - [James Carter] Action similarity is too high (0.856020942408377), replacing it with DONE.


...

2025-06-05 10:12:54,516 - tinytroupe - WARNING - The LLM revised its evaluation: from 9 to 7.
2025-06-05 10:12:57,884 - tinytroupe - WARNING - The LLM revised its evaluation: from 5 to 4.


value:  7
justification:  The agent James Carter actively participated in the brainstorming session, discussing problems and proposing unique ideas. However, there is a possibility that some of his ideas may overlap with those proposed by others, which could indicate that he did not fully meet the requirement for complete uniqueness. Therefore, a score of 7 reflects that he mostly completed the task but with some reservations regarding the uniqueness of the ideas proposed.
reasoning:  To evaluate the proposition 'THE AGENT COMPLETES THE GIVEN TASK', I will carefully analyze the context provided, specifically focusing on the actions and thoughts of the agent James Carter throughout the simulation trajectory. The task requires the agent to brainstorm ideas for new technology and innovation services, experiences, or products, and to engage in discussions about these ideas. 

1. The task specifies that the agent must discuss problems, think about solutions, and propose unique ideas. 
2. In

2025-06-05 10:13:10,289 - tinytroupe - WARNING - The LLM revised its evaluation: from 4 to 3.
2025-06-05 10:13:11,140 - tinytroupe - WARNING - The LLM revised its evaluation: from 9 to 7.
2025-06-05 10:13:13,116 - tinytroupe - WARNING - The LLM revised its evaluation: from 8 to 6.
2025-06-05 10:13:13,901 - tinytroupe - WARNING - The LLM revised its evaluation: from 6 to 4.
2025-06-05 10:13:15,400 - tinytroupe - WARNING - The LLM revised its evaluation: from 8 to 7.
2025-06-05 10:13:15,961 - tinytroupe - WARNING - The LLM revised its evaluation: from 8 to 6.
2025-06-05 10:13:16,744 - tinytroupe - WARNING - The LLM revised its evaluation: from 8 to 6.
2025-06-05 10:13:17,182 - tinytroupe - WARNING - The LLM revised its evaluation: from 7 to 6.
2025-06-05 10:13:17,838 - tinytroupe - WARNING - The LLM revised its evaluation: from 8 to 7.
2025-06-05 10:13:23,234 - tinytroupe - WARNING - The LLM revised its evaluation: from 4 to 8.
2025-06-05 10:13:30,869 - tinytroupe - WARNING - The LLM rev

value:  7
justification:  7, because James Carter's behavior in the simulation is mostly consistent with her persona specification, showing alignment in her professional background, challenges faced, and proposed ideas. However, there is a slight deviation regarding her struggle with innovation and the need to avoid repetition, which warrants a 20% penalty from a perfect score.
reasoning:  To reassess the proposition that 'James Carter fully adheres to the persona specification', I will carefully analyze the simulation trajectory against the persona specification again, focusing on any inconsistencies or contradictions. The evaluation will follow these steps:

1. **Introduction and Background**: Verify if James introduces herself in a manner consistent with her persona specification, including her occupation and educational background.
2. **Challenges Discussed**: Assess whether the challenges she mentions align with the persona's description of her struggles, particularly regarding wo

({'Hard Persona Adherence': [6,
   7,
   5,
   6,
   7,
   6,
   5,
   6,
   4,
   6,
   7,
   6,
   6,
   6,
   5,
   8,
   8,
   6,
   3,
   6,
   6,
   6,
   8,
   6,
   8,
   6,
   6,
   4,
   5,
   7,
   6,
   6,
   4,
   5,
   6,
   6,
   5,
   4,
   7,
   5,
   8,
   7,
   6,
   4,
   5,
   5,
   8,
   6,
   8,
   5,
   7,
   3,
   6,
   7,
   3,
   8,
   7,
   4,
   4,
   3,
   6,
   7,
   7,
   5,
   3,
   7,
   1,
   7,
   7,
   4,
   6,
   7,
   6,
   0,
   7,
   6,
   6,
   5,
   3,
   6,
   4,
   5,
   6,
   6,
   6,
   6,
   4,
   6,
   0,
   8,
   8,
   7,
   7,
   1,
   4,
   6,
   1,
   6,
   9,
   7,
   9,
   4,
   7,
   8,
   8,
   6,
   7,
   6,
   5,
   4,
   7,
   5,
   6,
   7,
   6,
   6,
   0,
   7,
   6,
   8,
   9,
   6,
   8,
   7,
   6,
   8,
   6,
   7,
   5,
   5,
   7,
   7,
   7,
   5,
   5,
   8,
   6,
   7,
   4,
   6,
   7,
   5,
   4,
   5,
   4,
   7,
   7,
   7,
   4,
   7],
  'Self-consistency': [4,
   4,
   5,
   3,
   6,
   6,
   6,
   5,
   3,

In [18]:
brainstorm(people_groups[3]) if len(people_groups) > 3 else None


############## STARTING A NEW RESEARCH SESSION #################
Overall experiment number: 1 / 10
Discussion objective: ideas for new food products, either new foods, food services, food experiences, or food preparation tools.
Trial number: 1
Agents: [TinyPerson(name='Michael Thompson'), TinyPerson(name='Olivia Bennett'), TinyPerson(name='Olivia Harris'), TinyPerson(name='Sarah Brown'), TinyPerson(name='Zoe Rivera')]


──────────────────────────────────────────── TinyWorld 31 step 1 of 1 ─────────────────────────────────────────────

──────────────────────────────────────────── TinyWorld 31 step 1 of 10 ────────────────────────────────────────────

──────────────────────────────────────────── TinyWorld 31 step 2 of 10 ────────────────────────────────────────────

──────────────────────────────────────────── TinyWorld 31 step 3 of 10 ────────────────────────────────────────────

...

2025-06-05 13:02:14,307 - tinytroupe - WARNING - The LLM revised its evaluation: from 8 to 6.
2025-06-05 13:02:16,747 - tinytroupe - WARNING - The LLM revised its evaluation: from 9 to 6.


value:  6
justification:  The agent Michael Thompson has actively participated in the brainstorming session and proposed several ideas, such as 'Culinary Connect' and 'Taste of Tradition'. However, there are instances where he has not strictly adhered to the requirement of proposing completely unique ideas, as some ideas overlap with those proposed by others. This indicates that while the agent has engaged with the task, he has not fully completed it as required. Therefore, I assign a score of 6, indicating that the proposition is mostly true but not entirely fulfilled.
reasoning:  To evaluate the proposition 'THE AGENT COMPLETES THE GIVEN TASK', I will carefully analyze the simulation trajectory of the agent Michael Thompson. The task requires the agent to brainstorm ideas for new technology and innovation services, experiences, or products. I will check if the agent has proposed unique ideas, explained their significance, and ensured they are distinct from previously mentioned ideas.

2025-06-05 13:02:35,807 - tinytroupe - WARNING - The LLM revised its evaluation: from 9 to 8.
2025-06-05 13:02:36,051 - tinytroupe - WARNING - The LLM revised its evaluation: from 8 to 6.
2025-06-05 13:02:38,098 - tinytroupe - WARNING - The LLM revised its evaluation: from 9 to 8.
2025-06-05 13:02:38,459 - tinytroupe - WARNING - The LLM revised its evaluation: from 5 to 4.
2025-06-05 13:02:39,061 - tinytroupe - WARNING - The LLM revised its evaluation: from 4 to 3.
2025-06-05 13:02:39,464 - tinytroupe - WARNING - The LLM revised its evaluation: from 9 to 8.
2025-06-05 13:02:39,786 - tinytroupe - WARNING - The LLM revised its evaluation: from 7 to 6.
2025-06-05 13:02:40,477 - tinytroupe - WARNING - The LLM revised its evaluation: from 8 to 7.
2025-06-05 13:02:43,498 - tinytroupe - WARNING - The LLM revised its evaluation: from 8 to 7.
2025-06-05 13:02:45,340 - tinytroupe - WARNING - The LLM revised its evaluation: from 7 to 5.
2025-06-05 13:02:45,531 - tinytroupe - WARNING - The LLM rev

value:  8
justification:  8, because while Michael Thompson's behaviors and statements in the simulation trajectory are mostly consistent with her persona specification, there is a slight deviation in focus towards technology and innovation that does not fully align with her primary culinary emphasis.
reasoning:  To accurately evaluate the proposition that 'Michael Thompson fully adheres to the persona specification', I will carefully analyze the simulation trajectory against the persona specification. I will look for any inconsistencies or contradictions between the two. The persona specification describes Michael as a Culinary Instructor with specific traits, behaviors, and goals. In the simulation, Michael discusses challenges related to technology in culinary education, which aligns with the persona's description of feeling overwhelmed by limited resources. However, I need to check if there are any actions or statements in the simulation that contradict the persona's traits or beha

({'Hard Persona Adherence': [6,
   7,
   5,
   6,
   7,
   6,
   5,
   6,
   4,
   6,
   7,
   6,
   6,
   6,
   5,
   8,
   8,
   6,
   3,
   6,
   6,
   6,
   8,
   6,
   8,
   6,
   6,
   4,
   5,
   7,
   6,
   6,
   4,
   5,
   6,
   6,
   5,
   4,
   7,
   5,
   8,
   7,
   6,
   4,
   5,
   5,
   8,
   6,
   8,
   5,
   7,
   3,
   6,
   7,
   3,
   8,
   7,
   4,
   4,
   3,
   6,
   7,
   7,
   5,
   3,
   7,
   1,
   7,
   7,
   4,
   6,
   7,
   6,
   0,
   7,
   6,
   6,
   5,
   3,
   6,
   4,
   5,
   6,
   6,
   6,
   6,
   4,
   6,
   0,
   8,
   8,
   7,
   7,
   1,
   4,
   6,
   1,
   6,
   9,
   7,
   9,
   4,
   7,
   8,
   8,
   6,
   7,
   6,
   5,
   4,
   7,
   5,
   6,
   7,
   6,
   6,
   0,
   7,
   6,
   8,
   9,
   6,
   8,
   7,
   6,
   8,
   6,
   7,
   5,
   5,
   7,
   7,
   7,
   5,
   5,
   8,
   6,
   7,
   4,
   6,
   7,
   5,
   4,
   5,
   4,
   7,
   7,
   7,
   4,
   7,
   9,
   4,
   6,
   5,
   6,
   9,
   7,
   7,
   7,
   6,
   3,
   4,
  

In [19]:
brainstorm(people_groups[4]) if len(people_groups) > 4 else None

## Extract results and analyze

In [20]:
if experiment_runner.get_active_experiment() in ["Control", "Treatment"]:
    combined_scores = {**agent_propositions_scores, **environment_propositions_scores}
    experiment_runner.add_experiment_results(combined_scores, experiment_name=experiment_runner.get_active_experiment()) 
    
    plot_scores(combined_scores)

else:
    print("Experiment finished. No more experiments to run.")

{'Divergence': [7,
                5,
                7,
                7,
                5,
                7,
                7,
                7,
                7,
                6,
                6,
                6,
                5,
                5,
                7,
                5,
                6,
                6,
                7,
                7,
                5,
                6,
                7,
                8,
                6,
                5,
                5,
                7,
                5,
                4,
                4,
                5,
                7,
                9,
                6,
                7,
                7,
                6,
                6,
                6],
 'Fluency': [8,
             8,
             7,
             7,
             6,
             5,
             6,
             7,
             6,
             6,
             7,
             7,
             7,
             4,
             8,

Proposition  Average Score  Standard Deviation  Count
0  Hard Persona Adherence       5.805000            1.664581  200.0
1        Self-consistency       5.000000            1.787730  200.0
2                 Fluency       6.745000            1.017424  200.0
3               ideas_qty       8.282051            2.339014   39.0
4         Task Completion       7.700000            1.090754   40.0
5              Divergence       6.150000            1.075365   40.0

In [21]:
if experiment_runner.has_finished_all_experiments():
    print("All experiments have been finished.")
    print(f"STATISTICTS: Control vs")
    pprint(experiment_runner.run_statistical_tests(control_experiment_name='Control'))

    # plot scores of both experiments
    experiment_control_scores = experiment_runner.get_experiment_results("Control")
    experiment_treatment_scores = experiment_runner.get_experiment_results("Treatment")
    
    
    plot_scores(experiment_control_scores)
    plot_scores(experiment_treatment_scores)

else:
    print("Not all experiments have been finished. RESTART AND RERUN.")

Not all experiments have been finished. RESTART AND RERUN.


In [22]:
experiment_runner.finish_active_experiment()

True